In [ ]:
import requests
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import re
import folium
import json
from folium import plugins
import geopy.distance
import seaborn as sns
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
import requests
import json
import pandas as pd
from geopy.geocoders import Nominatim
import csv
import os

Get Latitudes and Longitudes of cities in the UK

In [ ]:
#Function for Latitudes
def get_latitudes(cities):
    geolocator = Nominatim(user_agent="city_locator_latitudes")
    latitudes = []

    for city in cities:
        location = geolocator.geocode(city)
        if location:
            latitudes.append(location.latitude)
        else:
            latitudes.append(None)

    return latitudes

#Function for Longitudes
def get_longitudes(cities):
    geolocator = Nominatim(user_agent="city_locator_longitudes")
    longitudes = []

    for city in cities:
        location = geolocator.geocode(city)
        if location:
            longitudes.append(location.longitude)
        else:
            longitudes.append(None)

    return longitudes

cities = [
    "Bath", "Birmingham", "Bradford", "Brighton & Hove", "Bristol", "Cambridge", "Canterbury",
    "Carlisle", "Chelmsford", "Chester", "Chichester", "Colchester", "Coventry", "Derby",
    "Doncaster", "Durham", "Ely", "Exeter", "Gloucester", "Hereford", "Kingston-upon-Hull",
    "Lancaster", "Leeds", "Leicester", "Lichfield", "Lincoln", "Liverpool", "London",
    "Manchester", "Milton Keynes", "Newcastle-upon-Tyne", "Norwich", "Nottingham", "Oxford",
    "Peterborough", "Plymouth", "Portsmouth", "Preston", "Ripon", "Salford", "Salisbury",
    "Sheffield", "Southampton", "Southend-on-Sea", "Saint Albans", "Stoke on Trent",
    "Sunderland", "Truro", "Wakefield", "Wells", "Westminster", "Winchester", "Wolverhampton",
    "Worcester", "York", "Armagh", "Bangor", "Belfast", "Lisburn", "Londonderry", "Newry",
    "Aberdeen", "Dundee", "Dunfermline", "Edinburgh", "Glasgow", "Inverness", "Perth",
    "Stirling", "Bangor", "Cardiff", "Newport", "Saint Asaph", "Saint Davids", "Swansea",
    "Wrexham", "Douglas"
]


# Get latitudes and longitudes separately
latitudes = get_latitudes(cities)
longitudes = get_longitudes(cities)

# Combine Latitudes into a DataFrame
df_latitude = pd.DataFrame({
    'City': cities,
    'Latitude': latitudes
})

# Combine Longitudes into a DataFrame
df_longitude = pd.DataFrame({
    'City': cities,
    'Longitude': longitudes
})

print(df_latitude)
print(df_longitude)


               City   Latitude
0              Bath  51.381386
1        Birmingham  52.479699
2          Bradford  53.794423
3   Brighton & Hove  50.828860
4           Bristol  51.453802
..              ...        ...
72      Saint Asaph  40.003144
73     Saint Davids  40.040943
74          Swansea  51.619596
75          Wrexham  53.046508
76          Douglas  39.762842

[77 rows x 2 columns]
               City  Longitude
0              Bath  -2.359696
1        Birmingham  -1.902691
2          Bradford  -1.751919
3   Brighton & Hove  -0.140739
4           Bristol  -2.597298
..              ...        ...
72      Saint Asaph -75.226708
73     Saint Davids -75.378523
74          Swansea  -3.945925
75          Wrexham  -2.993787
76          Douglas -88.217052

[77 rows x 2 columns]


Get the store details in cities of the UK

In [ ]:
#Final Code

def get_store_lat_lngs(city, lat, lng):
    request = f'https://www.starbucks.com/bff/locations?features=DT&lat={lat}&lng={lng}&place={city},%20UK'

    headers = {
        'authority': 'www.starbucks.com',
        'method': 'GET',
        'path': f'/bff/locations?features=DT&lat={lat}&lng={lng}&place={city},%20UK',
        'scheme': 'https',
        'accept': 'application/json',
        'accept-encoding': 'gzip, deflate, br, zstd',
        'accept-language': 'en-US,en;q=0.9',
        'priority': 'u=1, i',
        'referer': f'https://www.starbucks.com/store-locator?features=DT&map={lat},{lng},5z&place={city},%20UK',
        'sec-ch-ua': '"Not)A;Brand";v="99", "Google Chrome";v="127", "Chromium";v="127"',
        'sec-ch-ua-mobile': '?1',
        'sec-ch-ua-platform': '"Android"',
        'sec-fetch-dest': 'empty',
        'sec-fetch-mode': 'cors',
        'sec-fetch-site': 'same-origin',
        'user-agent': 'Mozilla/5.0 (Linux; Android 6.0; Nexus 5 Build/MRA58N) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/127.0.0.0 Mobile Safari/537.36',
        'x-kl-ajax-request': 'Ajax_Request',
        'x-requested-with': 'XMLHttpRequest'
    }

    # Logging the request URL and headers
    print(f"Request URL: {request}")
    print(f"Request Headers: {headers}")

    response = requests.get(request, headers=headers)

    # Logging the response status and content
    print(f"Response Status Code: {response.status_code}")
    if response.status_code != 200:
        print(f"Failed to retrieve data for {city}. Status Code: {response.status_code}")
        return []

    # Logging the raw JSON response
    print("Raw JSON response:", response.text)

    # Parse the JSON response
    try:
        stores_data = response.json()
        print("Parsed JSON response:", stores_data)

        # Extract the required information
        extracted_data = []
        for store_info in stores_data:
            store = store_info.get('store', {})
            id = store.get('id')
            name = store.get('name')
            address = store.get('address', {}).get('singleLine')
            open_status = store.get('openStatusFormatted')
            hours_status = store.get('hoursStatusFormatted')
            latitude = store.get('coordinates', {}).get('latitude')
            longitude = store.get('coordinates', {}).get('longitude')
            isOpen24Hours = store.get('isOpen24Hours')

            extracted_data.append({
                'id':id,
                'name': name,
                'address': address,
                'openStatusFormatted': open_status,
                'hoursStatusFormatted': hours_status,
                'latitude': latitude,
                'longitude': longitude,
                'Hour24_Service': isOpen24Hours
            })

        # Display the extracted data
        for data in extracted_data:
            print(data)

        # Define the CSV file path
        csv_file_path = 'stores_data.csv'

        # Check if the file already exists to determine if the header should be written
        file_exists = os.path.isfile(csv_file_path)

        # Write the extracted data to a CSV file
        with open(csv_file_path, 'a', newline='', encoding='utf-8') as csvfile:
            fieldnames = ['id','name', 'address', 'openStatusFormatted', 'hoursStatusFormatted', 'latitude', 'longitude','Hour24_Service']
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

            # Write the header only if the file does not already exist
            if not file_exists:
                writer.writeheader()

            for data in extracted_data:
                writer.writerow(data)

        print(f"Data has been written to {csv_file_path}")

        return extracted_data

    except json.JSONDecodeError as e:
        print(f"Failed to parse JSON response for {city}: {e}")
        return []
# Loop through each city and get the store details
all_store_details = {}
for city in cities:
    print(f"Getting data for {city}")
    latitude = df_latitude[df_latitude['City'] == city]['Latitude'].values[0]
    longitude = df_longitude[df_longitude['City'] == city]['Longitude'].values[0]
    store_details = get_store_lat_lngs(city, latitude, longitude)
    print(f"Found {len(store_details)} stores in {city}")
    all_store_details[city] = store_details

# Count the total number of coordinates
total_coordinates = sum(len(details) for details in all_store_details.values())
print(f"Total coordinates found: {total_coordinates}")


Getting data for Bath
Request URL: https://www.starbucks.com/bff/locations?features=DT&lat=51.3813864&lng=-2.3596963&place=Bath,%20UK
Request Headers: {'authority': 'www.starbucks.com', 'method': 'GET', 'path': '/bff/locations?features=DT&lat=51.3813864&lng=-2.3596963&place=Bath,%20UK', 'scheme': 'https', 'accept': 'application/json', 'accept-encoding': 'gzip, deflate, br, zstd', 'accept-language': 'en-US,en;q=0.9', 'cookie': 'your_cookie_here', 'newrelic': 'your_newrelic_here', 'priority': 'u=1, i', 'referer': 'https://www.starbucks.com/store-locator?features=DT&map=51.3813864,-2.3596963,5z&place=Bath,%20UK', 'sec-ch-ua': '"Not)A;Brand";v="99", "Google Chrome";v="127", "Chromium";v="127"', 'sec-ch-ua-mobile': '?1', 'sec-ch-ua-platform': '"Android"', 'sec-fetch-dest': 'empty', 'sec-fetch-mode': 'cors', 'sec-fetch-site': 'same-origin', 'traceparent': 'your_traceparent_here', 'tracestate': 'your_tracestate_here', 'user-agent': 'Mozilla/5.0 (Linux; Android 6.0; Nexus 5 Build/MRA58N) Apple